# Lab 3: Introduction to Julia

There are traditionally two categories of computer languages: Compiled (C/C++, Fortran) and Interpreted (Python, R).

Julia language has inherited the advantage from both categories.

Some helpful links:
 * Julia documentation (https://julialang.org/)
 * Julia analysis demo at PyHEP 2023 (https://github.com/Moelf/PyHEP_2023_JuliaDemo/blob/main/Julia_analysis_demo.ipynb)
 * Talk (https://jiling.web.cern.ch/jiling/dump/2021_Harvard_JuliaHEP.html)
 

## Motivation

![](julia_comparison.png)
Ref: https://arxiv.org/abs/2109.09973

Julia is a solution to the "two-language problem," e.g. using writing performant C++ code and a high-level Python wrapper.

Consider this function taken from Numba's introduction. Numba is great because:
- you don't write C++
- you can write fast loop!

#### Python (Numba)
```python
@jit(nopython=True)
def go_fast(a):
    trace = 0.0
    for i in range(a.shape[0]):
        trace += np.tanh(a[i, i])
    return a + trace

In [2]: x = np.arange(100).reshape(10, 10)
In [3]: %timeit go_fast(x)
814 ns ± 5.2 ns (mean ± σ)    # Numba
16500 ns ± 70.5 ns (mean ± σ) # CPython
```

but it does have draw back (all JIT x Python solutions do): it's not compatible with all Python.

the Julia "sale" is that:
- you still avoid C++
- you can write fast anything!*
- there's no compatibility issue and "unhandled" construct, it's just the language itself

#### Julia
```julia
function go_faster(a)
    trace = 0.0
    for i in axes(a, 1)
        trace += tanh(a[i, i])
    end
    return a .+ trace
end
julia> x = reshape(0:99, 10, 10)
julia> @benchmark go_faster($x)
158.947 ns ± 100.451 ns (mean ± σ) # σ due to GC

```

## Array basics

In [ ]:
# A function makerandom with two methods is declared.
# This looks just like two functions with the same name but with different arguments.
# An array r with n Float64 elements is declared; element i is referred to as r[i].
# The Base function round(T,m) rounds the number m to the closest integer and converts to type T (here Int)
# The Base function rand() generates (when given no arguments) a random Float64 in [0,1).
# The functional difference between the methods is Float64 (first) vs Float32 (second) numbers returned.
# In the second method r[i]=rand() implies a loss of precision from 64 to 32 bit Float.

 function makerandom(n::Int)
    r=Array{Float64}(undef,n)
    for i=1:n
       r[i]=rand()
    end
    return r
 end

 function makerandom(m::Float64)
    n=round(Int,m)
    r=Array{Float32}(undef,n)
    for i=1:n
       r[i]=rand()
    end
    return r
 end

In [ ]:
# The function is called twice, with different arguments (example of multiple dispatch).
# In each case 5 times; n is assigned an integer-constant value, type will be Int (Int64).
# The Base function convert(Float64,n) converts the integer n to a Float64.

 n=5
 m=convert(Float64,n)

# The function is called with Int argument (first method dispatched)
# a will be the 5-element Float64 array returned by the function

 a=makerandom(n)
 for i=1:n
    println(i,"  ",a[i])
 end

In [ ]:
# The function is called with Float64 argument (second method dispatched)
# b will be the 5-element Float32 array returned by the function

 a=makerandom(m)
 for i=1:n
    println(i,"  ",a[i])
 end

## Matrix multiplication

In [ ]:
# This function creates an n*n random matrix (similar to randomarray.jl but 2-dim array)

 function randmatrix(n::Int)
    mat=Array{Float64}(undef,n,n)
    for j=1:n
       for i=1:n
          mat[i,j]=rand()
       end
    end
    return mat
 end

# Ask for matrix size and read it (stdin = standard input) using readline
# Text input has to be parsed to a type (here Int)

 println("Give matrix size")
 n=3

In [ ]:
# Create two random matrices and their product
# Note that "*" is actual matrix multiplication

 a=randmatrix(n)
 b=randmatrix(n)
 c=a*b

# print the results

 println()
 println("A, B, A*B")
 for i=1:n
    println(a[i,:],"  ",b[i,:],"  ",c[i,:])
 end


In [ ]:
# Element-by-element operations can be done with "." added to operator
# Here element-by-element multiplication

 c=a.*b
 println()
 println("A, B, A elements multiplied by B elements")
 for i=1:n
    println(a[i,:],"  ",b[i,:],"  ",c[i,:])
 end

In [ ]:
# Matrix inverse using Base function inv()
# Multiply inverse of A by A to check if OK

 b=inv(a)
 c=a*b
 println()
 println("A, 1/A, A*(1/A)")
 for i=1:n
    println(a[i,:],"  ",b[i,:],"  ",c[i,:])
 end

## Intro to Monte Carlo Simulation
In physics, the term ”Monte Carlo” refers to the use of random numbers. Monte
Carlo integration is the simplest of a wide range of ”Monte Carlo methods”, where averages are
calculated using uniform random sampling.

Monte Carlo simulation methods are related to the elementary Monte Carlo integration methods that we are discussing here, but are based on more efficient non-uniform sampling schemes. We will learn more about the detail in the later part of this course.

In [ ]:
# Calculates pi using a circle with radius r=1/2 (slightly faster than r=1) by MC sampling.

function pionebin(n) # samples and computes the average for one bin with n points
   sum=0
   for i=1:n
      x2=(rand()-0.5)^2
      y2=(rand()-0.5)^2
      if x2+y2 <= 0.25 
         sum=sum+1
      end
   end
   return 4.0*sum/n
end

In [ ]:
function samplepi(nbin,nsamp)  # Doing MC sampling of nbin bins, each sampling nsamp points
   av=0.
   er=0.    
   for j=1:nbin
      p=pionebin(nsamp)
      av=av+p
      er=er+p^2
      println(j,"   ",p)
   end
   av=av/nbin
   er=er/nbin
   er=((er-av^2)/(nbin-1))^0.5
   return av,er
end

In [ ]:
nbin=10
nsamp=10000

ap,ep=samplepi(nbin,nsamp)

println()
println("Final result and error:   ",ap,"   ",ep)

## Under the hood

Julia is able to show us what is happening "under the hood"

![](julia_compiler.png)

In [ ]:
function f(x)
    cos(x) + 2*x
end

In [ ]:
@code_typed f(2)

In [ ]:
@code_llvm f(2)

In [ ]:
@code_native f(2)